Parsing semantyczny z wykorzystaniem technik uczenia maszynowego
================================================================

Wprowadzenie
------------
Problem wykrywania slotów i ich wartości w wypowiedziach użytkownika można sformułować jako zadanie
polegające na przewidywaniu dla poszczególnych słów etykiet wskazujących na to czy i do jakiego
slotu dane słowo należy.

> chciałbym zarezerwować stolik na jutro**/day** na godzinę dwunastą**/hour** czterdzieści**/hour** pięć**/hour** na pięć**/size** osób

Granice slotów oznacza się korzystając z wybranego schematu etykietowania.

### Schemat IOB

| Prefix | Znaczenie                  |
|:------:|:---------------------------|
| I      | wnętrze slotu (inside)     |
| O      | poza slotem (outside)      |
| B      | początek slotu (beginning) |

> chciałbym zarezerwować stolik na jutro**/B-day** na godzinę dwunastą**/B-hour** czterdzieści**/I-hour** pięć**/I-hour** na pięć**/B-size** osób

### Schemat IOBES

| Prefix | Znaczenie                  |
|:------:|:---------------------------|
| I      | wnętrze slotu (inside)     |
| O      | poza slotem (outside)      |
| B      | początek slotu (beginning) |
| E      | koniec slotu (ending)      |
| S      | pojedyncze słowo (single)  |

> chciałbym zarezerwować stolik na jutro**/S-day** na godzinę dwunastą**/B-hour** czterdzieści**/I-hour** pięć**/E-hour** na pięć**/S-size** osób

Jeżeli dla tak sformułowanego zadania przygotujemy zbiór danych
złożony z wypowiedzi użytkownika z oznaczonymi slotami (tzw. *zbiór uczący*),
to możemy zastosować techniki (nadzorowanego) uczenia maszynowego w celu zbudowania modelu
annotującego wypowiedzi użytkownika etykietami slotów.

Do zbudowania takiego modelu można wykorzystać między innymi:

 1. warunkowe pola losowe (Lafferty i in.; 2001),

 2. rekurencyjne sieci neuronowe, np. sieci LSTM (Hochreiter i Schmidhuber; 1997),

 3. transformery (Vaswani i in., 2017).

Przykład
--------
Skorzystamy ze zbioru danych przygotowanego przez Schustera (2019).

In [1]:
!mkdir -p l07
%cd l07
!curl -L -C -  https://fb.me/multilingual_task_oriented_data  -o data.zip
%cd ..

C:\Users\Ania\Desktop\System_Dialogowy_Janet\l07


A subdirectory or file -p already exists.
Error occurred while processing: -p.
A subdirectory or file l07 already exists.
Error occurred while processing: l07.


C:\Users\Ania\Desktop\System_Dialogowy_Janet


** Resuming transfer from byte position 8923190
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed

  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0

  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
100    49  100    49    0     0     56      0 --:--:-- --:--:-- --:--:--   742


Zbiór ten gromadzi wypowiedzi w trzech językach opisane slotami dla dwunastu ram należących do trzech dziedzin `Alarm`, `Reminder` oraz `Weather`. Dane wczytamy korzystając z biblioteki [conllu](https://pypi.org/project/conllu/).

In [2]:
!pip3 install conllu
import codecs
from conllu import parse_incr
fields = ['id', 'form', 'frame', 'slot']

def nolabel2o(line, i):
    return 'O' if line[i] == 'NoLabel' else line[i]

with open('Janet_test.conllu', encoding='utf-8') as trainfile:
    trainset = list(parse_incr(trainfile, fields=fields, field_parsers={'slot': nolabel2o}))
with open('Janet_test.conllu', encoding='utf-8') as testfile:
    testset = list(parse_incr(testfile, fields=fields, field_parsers={'slot': nolabel2o}))

Zobaczmy kilka przykładowych wypowiedzi z tego zbioru.

In [3]:
!pip3 install tabulate
from tabulate import tabulate
tabulate(trainset[0], tablefmt='html')

'<table>\n<tbody>\n<tr><td style="text-align: right;">1</td><td>hej</td><td>greeting</td><td>O</td></tr>\n</tbody>\n</table>'

Na potrzeby prezentacji procesu uczenia w jupyterowym notatniku zawęzimy zbiór danych do początkowych przykładów.

Budując model skorzystamy z architektury opartej o rekurencyjne sieci neuronowe
zaimplementowanej w bibliotece [flair](https://github.com/flairNLP/flair) (Akbik i in. 2018).

In [4]:
!pip3 install flair

In [5]:
from flair.data import Corpus, Sentence, Token
from flair.datasets import SentenceDataset
from flair.embeddings import StackedEmbeddings
from flair.embeddings import WordEmbeddings
from flair.embeddings import CharacterEmbeddings
from flair.embeddings import FlairEmbeddings
from flair.models import SequenceTagger
from flair.trainers import ModelTrainer

!pip3 install torch
# determinizacja obliczeń
import random
import torch
random.seed(42)
torch.manual_seed(42)

if torch.cuda.is_available():
    torch.cuda.manual_seed(0)
    torch.cuda.manual_seed_all(0)
    torch.backends.cudnn.enabled = False
    torch.backends.cudnn.benchmark = False
    torch.backends.cudnn.deterministic = True

Dane skonwertujemy do formatu wykorzystywanego przez `flair`, korzystając z następującej funkcji.

In [6]:
def conllu2flair(sentences, label=None):
    fsentences = []

    for sentence in sentences:
        fsentence = Sentence()

        for token in sentence:
            ftoken = Token(token['form'])

            if label:
                ftoken.add_tag(label, token[label])

            fsentence.add_token(ftoken)

        fsentences.append(fsentence)

    return SentenceDataset(fsentences)

corpus = Corpus(train=conllu2flair(trainset, 'slot'), test=conllu2flair(testset, 'slot'))
print(corpus)
tag_dictionary = corpus.make_tag_dictionary(tag_type='slot')
print(tag_dictionary)

Corpus: 36 train + 4 dev + 40 test sentences
Dictionary with 13 tags: <unk>, O, B-appoinment/doctor, I-appoinment/doctor, B-datetime, I-datetime, B-login/id, B-appointment/type, I-appointment/type, B-prescription/type, B-login/password, <START>, <STOP>


Nasz model będzie wykorzystywał wektorowe reprezentacje słów (zob. [Word Embeddings](https://github.com/flairNLP/flair/blob/master/resources/docs/TUTORIAL_3_WORD_EMBEDDING.md)).

In [7]:
embedding_types = [
    WordEmbeddings('pl'),
    FlairEmbeddings('pl-forward'),
    FlairEmbeddings('pl-backward'),
    CharacterEmbeddings(),
]

embeddings = StackedEmbeddings(embeddings=embedding_types)
tagger = SequenceTagger(hidden_size=256, embeddings=embeddings,
                        tag_dictionary=tag_dictionary,
                        tag_type='slot', use_crf=True)

Zobaczmy jak wygląda architektura sieci neuronowej, która będzie odpowiedzialna za przewidywanie
slotów w wypowiedziach.

In [8]:
print(tagger)

SequenceTagger(
  (embeddings): StackedEmbeddings(
    (list_embedding_0): WordEmbeddings('pl')
    (list_embedding_1): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.25, inplace=False)
        (encoder): Embedding(1602, 100)
        (rnn): LSTM(100, 2048)
        (decoder): Linear(in_features=2048, out_features=1602, bias=True)
      )
    )
    (list_embedding_2): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.25, inplace=False)
        (encoder): Embedding(1602, 100)
        (rnn): LSTM(100, 2048)
        (decoder): Linear(in_features=2048, out_features=1602, bias=True)
      )
    )
    (list_embedding_3): CharacterEmbeddings(
      (char_embedding): Embedding(275, 25)
      (char_rnn): LSTM(25, 25, bidirectional=True)
    )
  )
  (word_dropout): WordDropout(p=0.05)
  (locked_dropout): LockedDropout(p=0.5)
  (embedding2nn): Linear(in_features=4446, out_features=4446, bias=True)
  (rnn): LSTM(4446, 256, batch_first=True, bidirectiona

Wykonamy dziesięć iteracji (epok) uczenia a wynikowy model zapiszemy w katalogu `slot-model`.

In [9]:
trainer = ModelTrainer(tagger, corpus)
trainer.train('slot-model',
              learning_rate=0.1,
              mini_batch_size=32,
              max_epochs=10,
              train_with_dev=False)

2021-05-16 11:40:14,273 ----------------------------------------------------------------------------------------------------
2021-05-16 11:40:14,274 Model: "SequenceTagger(
  (embeddings): StackedEmbeddings(
    (list_embedding_0): WordEmbeddings('pl')
    (list_embedding_1): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.25, inplace=False)
        (encoder): Embedding(1602, 100)
        (rnn): LSTM(100, 2048)
        (decoder): Linear(in_features=2048, out_features=1602, bias=True)
      )
    )
    (list_embedding_2): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.25, inplace=False)
        (encoder): Embedding(1602, 100)
        (rnn): LSTM(100, 2048)
        (decoder): Linear(in_features=2048, out_features=1602, bias=True)
      )
    )
    (list_embedding_3): CharacterEmbeddings(
      (char_embedding): Embedding(275, 25)
      (char_rnn): LSTM(25, 25, bidirectional=True)
    )
  )
  (word_dropout): WordDropout(p=0.05)
  (locked_dr

2021-05-16 11:41:12,575 BAD EPOCHS (no improvement): 2
2021-05-16 11:41:12,577 ----------------------------------------------------------------------------------------------------
2021-05-16 11:41:13,690 epoch 10 - iter 1/2 - loss 2.63941884 - samples/sec: 28.79 - lr: 0.100000
2021-05-16 11:41:13,878 epoch 10 - iter 2/2 - loss 2.18226165 - samples/sec: 171.12 - lr: 0.100000
2021-05-16 11:41:13,879 ----------------------------------------------------------------------------------------------------
2021-05-16 11:41:13,880 EPOCH 10 done: loss 2.1823 - lr 0.1000000
2021-05-16 11:41:13,906 DEV : loss 1.458857536315918 - score 0.0
2021-05-16 11:41:13,907 BAD EPOCHS (no improvement): 0
saving best model
2021-05-16 11:41:33,558 ----------------------------------------------------------------------------------------------------
2021-05-16 11:41:33,559 Testing using best model ...
2021-05-16 11:41:33,560 loading file slot-model\best-model.pt
2021-05-16 11:41:45,502 0.1765	0.1667	0.1714
2021-05-1

{'test_score': 0.17142857142857143,
 'dev_score_history': [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
 'train_loss_history': [11.51309585571289,
  5.878437042236328,
  7.245883822441101,
  3.1684603691101074,
  3.1224594116210938,
  4.798194766044617,
  1.9025391936302185,
  3.3012349605560303,
  2.347049653530121,
  2.182261645793915],
 'dev_loss_history': [5.320306777954102,
  2.201185703277588,
  2.3815672397613525,
  1.7660648822784424,
  1.8835055828094482,
  1.9106686115264893,
  1.5785303115844727,
  1.590420126914978,
  1.6068150997161865,
  1.458857536315918]}

Jakość wyuczonego modelu możemy ocenić, korzystając z zaraportowanych powyżej metryk, tj.:

 - *tp (true positives)*

   > liczba słów oznaczonych w zbiorze testowym etykietą $e$, które model oznaczył tą etykietą

 - *fp (false positives)*

   > liczba słów nieoznaczonych w zbiorze testowym etykietą $e$, które model oznaczył tą etykietą

 - *fn (false negatives)*

   > liczba słów oznaczonych w zbiorze testowym etykietą $e$, którym model nie nadał etykiety $e$

 - *precision*

   > $$\frac{tp}{tp + fp}$$

 - *recall*

   > $$\frac{tp}{tp + fn}$$

 - $F_1$

   > $$\frac{2 \cdot precision \cdot recall}{precision + recall}$$

 - *micro* $F_1$

   > $F_1$ w którym $tp$, $fp$ i $fn$ są liczone łącznie dla wszystkich etykiet, tj. $tp = \sum_{e}{{tp}_e}$, $fn = \sum_{e}{{fn}_e}$, $fp = \sum_{e}{{fp}_e}$

 - *macro* $F_1$

   > średnia arytmetyczna z $F_1$ obliczonych dla poszczególnych etykiet z osobna.

Wyuczony model możemy wczytać z pliku korzystając z metody `load`.

In [10]:
model = SequenceTagger.load('slot-model/final-model.pt')

2021-05-16 11:41:45,529 loading file slot-model/final-model.pt


Wczytany model możemy wykorzystać do przewidywania slotów w wypowiedziach użytkownika, korzystając
z przedstawionej poniżej funkcji `predict`.

In [11]:
def predict(model, sentence):
    csentence = [{'form': word} for word in sentence]
    fsentence = conllu2flair([csentence])[0]
    model.predict(fsentence)
    return [(token, ftoken.get_tag('slot').value) for token, ftoken in zip(sentence, fsentence)]


Jak pokazuje przykład poniżej model wyuczony tylko na 100 przykładach popełnia w dosyć prostej
wypowiedzi błąd etykietując słowo `alarm` tagiem `B-weather/noun`.

In [20]:
tabulate(predict(model, 'doktor lekarza rodzinnego najlepiej dzisiaj w godzinach popołudniowych dziś '.split()), tablefmt='html')

'<table>\n<tbody>\n<tr><td>doktor        </td><td>I-appoinment/doctor</td></tr>\n<tr><td>lekarza       </td><td>B-appoinment/doctor</td></tr>\n<tr><td>rodzinnego    </td><td>O                  </td></tr>\n<tr><td>najlepiej     </td><td>O                  </td></tr>\n<tr><td>dzisiaj       </td><td>O                  </td></tr>\n<tr><td>w             </td><td>O                  </td></tr>\n<tr><td>godzinach     </td><td>O                  </td></tr>\n<tr><td>popołudniowych</td><td>O                  </td></tr>\n<tr><td>dziś          </td><td>O                  </td></tr>\n</tbody>\n</table>'

Literatura
----------
 1. Sebastian Schuster, Sonal Gupta, Rushin Shah, Mike Lewis, Cross-lingual Transfer Learning for Multilingual Task Oriented Dialog. NAACL-HLT (1) 2019, pp. 3795-3805
 2. John D. Lafferty, Andrew McCallum, and Fernando C. N. Pereira. 2001. Conditional Random Fields: Probabilistic Models for Segmenting and Labeling Sequence Data. In Proceedings of the Eighteenth International Conference on Machine Learning (ICML '01). Morgan Kaufmann Publishers Inc., San Francisco, CA, USA, 282–289, https://repository.upenn.edu/cgi/viewcontent.cgi?article=1162&context=cis_papers
 3. Sepp Hochreiter and Jürgen Schmidhuber. 1997. Long Short-Term Memory. Neural Comput. 9, 8 (November 15, 1997), 1735–1780, https://doi.org/10.1162/neco.1997.9.8.1735
 4. Ashish Vaswani, Noam Shazeer, Niki Parmar, Jakob Uszkoreit, Llion Jones, Aidan N. Gomez, Lukasz Kaiser, Illia Polosukhin, Attention is All you Need, NIPS 2017, pp. 5998-6008, https://arxiv.org/abs/1706.03762
 5. Alan Akbik, Duncan Blythe, Roland Vollgraf, Contextual String Embeddings for Sequence Labeling, Proceedings of the 27th International Conference on Computational Linguistics, pp. 1638–1649, https://www.aclweb.org/anthology/C18-1139.pdf
